# MOSI UseCase

This notebooks :

- Creates UCD
- Creates UCD Schema 
- Insert MOSI Record
- Publishes

In [7]:
import requests
import json

# These parameters should be discovered / initialized by common gcube libraries. 
gcube_token = "3aa85bbf-d5f3-4df4-ad03-4f8f788eba3d-98187548"
service_base_endpoint ="https://geoportal.dev.int.d4science.net/geoportal-service/srv"

# Actual customizable parameters
ucid = "GNA-MOSI"
gpkgFile = "templateItalia.gpkg"


#NB The following should not be changed 
projects_endpoint = service_base_endpoint + "/projects/"+ucid
ucd_endpoint = service_base_endpoint + "/ucd/"
plugins_endpoint=service_base_endpoint + "/plugins/"


## Import Rich text support for pretty json 
!pip install rich[jupyter]
import rich
from rich import print_json

## Define utility function for HTTP requests logging
def send(dest,data=None,method="GET",params={}):
    print("GOING TO SEND "+method+" REQUEST TO "+dest)
    headers={
        'Content-type':'application/json', 
        'Accept':'*/*',
        'gcube-token':gcube_token
    }
    if data is not None : print("Data is "+str(data))
    if method == "GET" : response = requests.get(url=dest,params=params,headers=headers)
    if method == "PUT" : response = requests.put(url=dest,data=data,params=params,headers=headers)
    if method == "POST" : response = requests.post(url=dest,data=data,params=params,headers=headers)
    if method == "DELETE" : response = requests.delete(url=dest,data=data,params=params,headers=headers)
    print("RESPONSE STATUS "+str(response.status_code))    
    if response.status_code<200 or response.status_code>=300 : 
           print("CAUSE "+str(response.reason))
           print(response.text)
    return json.loads(response.text)

#print(send(method="GET",dest="http://geoportal.dev.int.d4science.net/geoportal-service/srv/mongo-concessioni/"))

In [ ]:
# GPKG support
import fiona


In [2]:
# Init parameters
UCD = {
  "_id" : ucid,
  "_version" : "1.0.0",
  "_name" : "GNA : MOSI",

  "_description" : "Modulistica siti",





  "_handlers" : [
    ,
    
  ]
}

## UCD

In [3]:
schema={
    "CD" : {"_min":1, "label" : "Identificazione","_children" :[
                             {"TSK" : {"_min":1,"_type" : "STRING-CONSTANT", "value":{"MOSI"},"label":"Tipo modulo"}},
                             {"CMD" : {"_min":1,"label":"Codice modulo"}}, # ?? Auto generate
                             {"ESC" : {"_min":1,"label":"Ente schedatore"}}, # ?? Auto generate
                             {"ECP" : {"_min":1,"label":"Ente competente per tutela"}}, # ?? Auto generate
                             {"CBC" : {"label":"Identificativo scheda bene culturale"}},
                             {"ACC" : {"_max":-1,"label":"Altro codice", "_children"}}
                             
                         ]
    }
}
#NB Cannot set schema from gpkg.MOSI if we want it structured
#with fiona.open(gpkgFile, layer='MOSI_multipolygon') as layer:
#    feature = layer[0]
    #feature is GeoJSON




# SET GEOMETR        
schema.update("multipolygonGeometries":{"_max":-1})
schema.update("points":{"_max":-1})
schema.update("multipolygonGeometries":{"_max":-1})




UCD.update({"_schema" :schema})

In [4]:
#TODO DEFINE ROLES
UCD.update({"_dataAccessPolicies" : [
    {"_policy" : {"_read" : "own", "_write" : "own"}, "_roles":[]},
  ]})

In [5]:
# UPDATE Lifecycle Settings
UCD["_handlers"].append({
      "_id" :  "DEFAULT-SINGLE-STEP",
      "_type" :  "LifecycleManagement",
      "_configuration" : {
        "step_access" : [
          {"STEP" : "PUBLISH", "roles" :[]}
        ]
      }
    })

In [6]:
# UPDATE Lifecycle Settings
UCD["_handlers"].append({
      "_id" : "SDI-Indexer-Plugin",
      "_type" : "Indexer",
      "_configuration" : {
# TODO use 
#     "bboxEvaluation" : ["$..posizionamentoScavo.._bbox"],
        "explicitFieldMapping" : [
#TODO READ FROM MOSI LAYER 
        ],
        "additionalLayers" : [
# TODO CONFIGURE Additional
          {"source" : {"url" :  "..."},"toSetTitle":""}
        ]
      }
    }
    })

SyntaxError: closing parenthesis '}' does not match opening parenthesis '(' on line 2 (3773975152.py, line 17)